<h1 align=center><font size = 5>Segmenting and Clustering Neighborhoods in the City of Los Angeles</font></h1>

## Introduction

In this project I converted Los Angeles(LA) addresses into their equivalent latitude and longitude values. Then I used the Foursquare API to explore neighborhoods in LA, used the **explore** function to get the most common venue categories in each neighborhood. I then used this feature to group the neighborhoods and clusters using *k*-means clustering algorithm. The Folium library was used to visualize the neighborhoods in LA and their emerging clusters.

## Table of Contents

<div class="alert alert-block alert-info" style="margin-top: 20px">

<font size = 3>

1. <a href="#item1">Download and Explore Dataset</a>

2. <a href="#item2">Explore Neighborhoods in LA</a>

3. <a href="#item3">Analyze Each Neighborhood</a>

4. <a href="#item4">Cluster Neighborhoods</a>

5. <a href="#item5">Examine Clusters</a>    
</font>
</div>

Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.8.3
  latest version: 4.8.4

Please update conda by running

    $ conda update -n base -c defaults conda



## Package Plan ##

  environment location: /home/jupyterlab/conda/envs/python

  added / updated specs:
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    geopy-2.0.0                |     pyh9f0ad1d_0          63 KB  conda-forge
    openssl-1.1.1g             |       h516909a_1         2.1 MB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.2 MB

The following NEW packages will be INSTALLED:

  geographiclib      conda-forge/noarch::geographiclib-1.50-py_0
  geopy              conda-forge/noarch::geopy-2.0.0

<a id='item1'></a>

## 1. Download and Explore Dataset

In order to segment the neighborhoods and explore them, we will essentially need a dataset that contains the neighborhoods that exist as well as the latitude and longitude coordinates of each neighborhood.

The dataset was found here: https://usc.data.socrata.com/dataset/Los-Angeles-Neighborhood-Map/r8qd-yxsr

In [2]:
url = 'https://usc.data.socrata.com/api/geospatial/r8qd-yxsr?method=export&format=GeoJSON'
url

'https://usc.data.socrata.com/api/geospatial/r8qd-yxsr?method=export&format=GeoJSON'

#### Load and explore the data

Next, let's load the data.

In [3]:
la_data = requests.get(url).json()

Let's take a quick look at the data.

In [4]:
la_data

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'properties': {'external_i': 'acton',
    'name': 'Acton',
    'location': 'POINT(34.497355239240846 -118.16981019229348)',
    'latitude': '-118.16981019229348',
    'slug_1': None,
    'sqmi': '39.3391089485',
    'display_na': 'Acton L.A. County Neighborhood (Current)',
    'set': 'L.A. County Neighborhoods (Current)',
    'slug': 'acton',
    'longitude': '34.497355239240846',
    'name_1': None,
    'kind': 'L.A. County Neighborhood (Current)',
    'type': 'unincorporated-area'},
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [[[[-118.20261747920541, 34.53898972076929],
       [-118.18946958918568, 34.5385546636616],
       [-118.18950400422953, 34.5349457732411],
       [-118.185124836341, 34.53482956044709],
       [-118.18516440876348, 34.53124651970553],
       [-118.17601577983017, 34.531354702430015],
       [-118.1761893084381, 34.523803185624594],
       [-118.16702561365965, 34.52351227823281],

Notice how all the relevant data is in the *features* key, which is basically a list of the neighborhoods. So, let's define a new variable that includes this data.

In [5]:
neighborhoods_data = la_data['features']

Let's take a look at the first item in this list.

In [6]:
neighborhoods_data[0]

{'type': 'Feature',
 'properties': {'external_i': 'acton',
  'name': 'Acton',
  'location': 'POINT(34.497355239240846 -118.16981019229348)',
  'latitude': '-118.16981019229348',
  'slug_1': None,
  'sqmi': '39.3391089485',
  'display_na': 'Acton L.A. County Neighborhood (Current)',
  'set': 'L.A. County Neighborhoods (Current)',
  'slug': 'acton',
  'longitude': '34.497355239240846',
  'name_1': None,
  'kind': 'L.A. County Neighborhood (Current)',
  'type': 'unincorporated-area'},
 'geometry': {'type': 'MultiPolygon',
  'coordinates': [[[[-118.20261747920541, 34.53898972076929],
     [-118.18946958918568, 34.5385546636616],
     [-118.18950400422953, 34.5349457732411],
     [-118.185124836341, 34.53482956044709],
     [-118.18516440876348, 34.53124651970553],
     [-118.17601577983017, 34.531354702430015],
     [-118.1761893084381, 34.523803185624594],
     [-118.16702561365965, 34.52351227823281],
     [-118.16294026595281, 34.523716853632315],
     [-118.16298888279476, 34.527586918

#### Tranform the data into a *pandas* dataframe

We transform this data of nested Python dictionaries into a *pandas* dataframe by creating an empty dataframe.

In [7]:
# define the dataframe columns
column_names = ['Neighborhood', 'Latitude', 'Longitude'] 
# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

Take a look at the empty dataframe to confirm that the columns are as intended.

In [8]:
neighborhoods

Empty DataFrame
Columns: [Neighborhood, Latitude, Longitude]
Index: []

Then let's loop through the data and fill the dataframe one row at a time.

In [9]:
for data in neighborhoods_data:
    # borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
    neighborhood_lon = data['properties']['latitude']
    neighborhood_lat = data['properties']['longitude']
    neighborhoods = neighborhoods.append({'Neighborhood': neighborhood_name,
                                          'Latitude': float(neighborhood_lat),
                                          'Longitude': float(neighborhood_lon)}, ignore_index=True)
#locations = df_counters[['latitude', 'longitude']] locationlist = locations.values.tolist() locationlist = [[float(lat),float(lon)] for [lat,lon] in locationlist] 

Quickly examine the resulting dataframe.

In [10]:
neighborhoods.head()

Neighborhood   Latitude   Longitude
0            Acton  34.497355 -118.169810
1  Adams-Normandie  34.031461 -118.300208
2     Agoura Hills  34.146736 -118.759885
3       Agua Dulce  34.504927 -118.317104
4         Alhambra  34.085539 -118.136512

We make sure that the dataset ia cleaned of unwanted rows.

In [11]:
neighborhoods.shape
neighborhoods = neighborhoods.dropna(how='any',axis=0)
neighborhoods.shape

(272, 3)

#### Use geopy library to get the latitude and longitude values of LA.

In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent <em>la_explorer</em>, as shown below.

In [12]:
address = 'Los Angeles, CA'

geolocator = Nominatim(user_agent="la_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Los Angeles are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Los Angeles are 34.0536909, -118.2427666.


#### Create a map of LA with neighborhoods superimposed on top.

In [13]:
# create map of LA using latitude and longitude values
map_la = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_la)  
    
map_la

Zoom into the above map, and click on each circle mark to reveal the name of the neighborhood.

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

#### Define Foursquare Credentials and Version

In [14]:
CLIENT_ID = 'ZKDGK54BN5E1W0NQSHEFVK0FZPJMHQYR2L1WSJRWPMJUOEXV' # your Foursquare ID
CLIENT_SECRET = 'CYJ5BAWFN5NEB5PPRQIAOAZLKKNSOOIICF0DYJQIO54GMXBV' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: ZKDGK54BN5E1W0NQSHEFVK0FZPJMHQYR2L1WSJRWPMJUOEXV
CLIENT_SECRET:CYJ5BAWFN5NEB5PPRQIAOAZLKKNSOOIICF0DYJQIO54GMXBV


#### Let's explore the first neighborhood in our dataframe.

Get the neighborhood's name.

In [15]:
neighborhood_latitude = neighborhoods.loc[0, 'Latitude']
neighborhood_longitude = neighborhoods.loc[0, 'Longitude']
neighborhood_name = neighborhoods.loc[0, 'Neighborhood']
neighborhood_name

'Acton'

Get the neighborhood's latitude and longitude values.

In [16]:
neighborhood_latitude = neighborhoods.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = neighborhoods.loc[0, 'Longitude'] # neighborhood longitude value
neighborhood_name = neighborhoods.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Acton are 34.49735523924085, -118.16981019229348.


#### Now, let's get the top 100 venues that are in Acton within a radius of 500 meters.

First, let's create the GET request URL. Name your URL **url**.

In [17]:
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL

'https://api.foursquare.com/v2/venues/explore?&client_id=ZKDGK54BN5E1W0NQSHEFVK0FZPJMHQYR2L1WSJRWPMJUOEXV&client_secret=CYJ5BAWFN5NEB5PPRQIAOAZLKKNSOOIICF0DYJQIO54GMXBV&v=20180605&ll=34.49735523924085,-118.16981019229348&radius=500&limit=100'

Double-click __here__ for the solution.
<!-- The correct answer is:
LIMIT = 100 # limit of number of venues returned by Foursquare API
-->

<!--
radius = 500 # define radius
-->

<!--
\\ # create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL
--> 

Send the GET request and examine the resutls

In [18]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5f484e827c1c9e0994b5e0f8'},
 'response': {'warning': {'text': "There aren't a lot of results near you. Try something more general, reset your filters, or expand the search area."},
  'headerLocation': 'Current map view',
  'headerFullLocation': 'Current map view',
  'headerLocationGranularity': 'unknown',
  'totalResults': 2,
  'suggestedBounds': {'ne': {'lat': 34.50185524374085,
    'lng': -118.16436022594964},
   'sw': {'lat': 34.492855234740844, 'lng': -118.17526015863733}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '5a326a84345cbe5681ec1aaf',
       'name': 'Epik Engineering',
       'location': {'address': '33945 McEnnery Canyon Rd',
        'lat': 34.498718,
        'lng': -118.16804599999999,
        'labeledLatLngs': [{'l

From the Foursquare lab in the previous module, we know that all the information is in the *items* key. Before we proceed, let's borrow the **get_category_type** function from the Foursquare lab.

In [19]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a *pandas* dataframe.

In [20]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


name                  categories        lat         lng
0    Epik Engineering  Construction & Landscaping  34.498718 -118.168046
1  Alma Gardening Co.  Construction & Landscaping  34.494762 -118.172550

And how many venues were returned by Foursquare?

In [21]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

2 venues were returned by Foursquare.


<a id='item2'></a>

## 2. Explore Neighborhoods in LA

#### Let's create a function to repeat the same process to all the neighborhoods in LA

In [22]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now write the code to run the above function on each neighborhood and create a new dataframe called *la_venues*.

In [23]:
la_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )



Acton
Adams-Normandie
Agoura Hills
Agua Dulce
Alhambra
Alondra Park
Artesia
Altadena
Angeles Crest
Arcadia
Arleta
Arlington Heights
Athens
Atwater Village
Avalon
Avocado Heights
Azusa
Vermont-Slauson
Baldwin Hills/Crenshaw
Baldwin Park
Bel-Air
Bellflower
Bell Gardens
Green Valley
Bell
Beverly Crest
Beverly Grove
Burbank
Koreatown
Beverly Hills
Beverlywood
Boyle Heights
Bradbury
Brentwood
Broadway-Manchester
Calabasas
Canoga Park
Carson
Carthay
Castaic Canyons
Chatsworth
Castaic
Central-Alameda
Century City
Cerritos
Charter Oak
Chatsworth Reservoir
Chesterfield Square
Cheviot Hills
Chinatown
Citrus
Claremont
Northridge
Commerce
Compton
Cypress Park
La Mirada
Covina
Cudahy
Culver City
Del Aire
Del Rey
Desert View Highlands
Diamond Bar
Downey
Downtown
Duarte
Eagle Rock
East Compton
East Hollywood
East La Mirada
Elizabeth Lake
East Los Angeles
East Pasadena
East San Gabriel
Echo Park
El Monte
El Segundo
El Sereno
Elysian Park
Elysian Valley
Vermont Square
Encino
Exposition Park
Fairfax
Flo

#### Let's check the size of the resulting dataframe

In [24]:
print(la_venues.shape)
la_venues.head()

(2974, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0            Acton              34.497355             -118.169810   
1            Acton              34.497355             -118.169810   
2  Adams-Normandie              34.031461             -118.300208   
3  Adams-Normandie              34.031461             -118.300208   
4  Adams-Normandie              34.031461             -118.300208   

                Venue  Venue Latitude  Venue Longitude  \
0    Epik Engineering       34.498718      -118.168046   
1  Alma Gardening Co.       34.494762      -118.172550   
2   Orange Door Sushi       34.032485      -118.299368   
3               Shell       34.033095      -118.300025   
4         Little Xian       34.032292      -118.299465   

               Venue Category  
0  Construction & Landscaping  
1  Construction & Landscaping  
2            Sushi Restaurant  
3                 Gas Station  
4            Sushi Restaurant

Let's check how many venues were returned for each neighborhood

In [25]:
la_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                   
Acton                                                      2   
Adams-Normandie                                           10   
Agoura Hills                                              27   
Agua Dulce                                                 1   
Alhambra                                                  14   
Alondra Park                                               1   
Altadena                                                   5   
Arcadia                                                   24   
Arleta                                                     4   
Arlington Heights                                         26   
Artesia                                                   33   
Athens                                                     1   
Atwater Village                                           22   
Avalon                                                     4   
Avocado Heights                                           12   
Azusa                                                      9   
Baldwin Hills/Crenshaw                                     4   
Baldwin Park                                               6   
Bel-Air                                                    3   
Bell                                                       1   
Bell Gardens                                              12   
Bellflower                                                15   
Beverly Grove                                            100   
Beverly Hills                                              1   
Beverlywood                                                4   
Boyle Heights                                              9   
Bradbury                                                   2   
Brentwood                                                  1   
Broadway-Manchester                                        6   
Burbank                                                   18   
Calabasas                                                  1   
Canoga Park                                               11   
Carthay                                                   21   
Central-Alameda                                            5   
Century City                                              59   
Cerritos                                                   3   
Charter Oak                                                3   
Chatsworth                                                 2   
Chesterfield Square                                        6   
Cheviot Hills                                              1   
Chinatown                                                 46   
Citrus                                                     5   
Commerce                                                   2   
Compton                                                   19   
Covina                                                    10   
Cudahy                                                     9   
Culver City                                               45   
Cypress Park                                               4   
Del Aire                                                  14   
Del Rey                                                   20   
Diamond Bar                                               37   
Downey                                                    43   
Downtown                                                  21   
Eagle Rock                                                 3   
East Compton                                               7   
East Hollywood                                            16   
East La Mirada                                             1   
East Los Angeles                                          13   
East Pasadena                                              1   
East San Gabriel                                          11   
Echo Park                                                 38   
El Mont

#### Let's find out how many unique categories can be curated from all the returned venues

In [26]:
print('There are {} uniques categories.'.format(len(la_venues['Venue Category'].unique())))
list(la_venues['Venue Category'].unique())

There are 323 uniques categories.


['Construction & Landscaping',
 'Sushi Restaurant',
 'Gas Station',
 'Taco Place',
 'Yoga Studio',
 'Bookstore',
 'Playground',
 'Grocery Store',
 'Park',
 'Fast Food Restaurant',
 'Café',
 'Indian Restaurant',
 'Restaurant',
 'Brewery',
 'Breakfast Spot',
 'BBQ Joint',
 'American Restaurant',
 'Bakery',
 'Burger Joint',
 'Multiplex',
 'Chinese Restaurant',
 'Thai Restaurant',
 'Mexican Restaurant',
 'Deli / Bodega',
 'Lounge',
 'Hotel',
 'Shipping Store',
 'Shopping Mall',
 'Airport',
 'Pizza Place',
 'Convenience Store',
 'Video Store',
 'Hardware Store',
 'Sporting Goods Shop',
 'Bagel Shop',
 'Pet Store',
 'Frozen Yogurt Shop',
 'Sandwich Place',
 'Salon / Barbershop',
 'Taiwanese Restaurant',
 'Asian Restaurant',
 'Vegetarian / Vegan Restaurant',
 'Vietnamese Restaurant',
 'Bubble Tea Shop',
 'Gift Shop',
 'Boutique',
 'Tea Room',
 'Bank',
 'Pharmacy',
 'Home Service',
 'Campground',
 'Food',
 'Notary',
 'Golf Course',
 'Football Stadium',
 'Japanese Restaurant',
 'Cosmetics Shop'

<a id='item3'></a>

## 3. Analyze Each Neighborhood

In [27]:
# one hot encoding
la_onehot = pd.get_dummies(la_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
la_onehot['Neighborhood'] = la_venues['Neighborhood'] 

# move neighborhood column to the first column
# fixed_columns = [la_onehot.columns[-1]] + list(la_onehot.columns[:-1])
# la_onehot = la_onehot[fixed_columns]

la_onehot.head(5)

ATM  Accessories Store  Airport  Airport Terminal  American Restaurant  \
0    0                  0        0                 0                    0   
1    0                  0        0                 0                    0   
2    0                  0        0                 0                    0   
3    0                  0        0                 0                    0   
4    0                  0        0                 0                    0   

   Amphitheater  Animal Shelter  Antique Shop  Arcade  Argentinian Restaurant  \
0             0               0             0       0                       0   
1             0               0             0       0                       0   
2             0               0             0       0                       0   
3             0               0             0       0                       0   
4             0               0             0       0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Athletics & Sports  Australian Restaurant  Auto Garage  \
0                 0                   0                      0            0   
1                 0                   0                      0            0   
2                 0                   0                      0            0   
3                 0                   0                      0            0   
4                 0                   0                      0            0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0              0                0          0           0           0       0   
1              0                0          0           0           0       0   
2              0                0          0           0           0       0   
3              0                0          0           0           0       0   
4              0                0          0           0           0       0   

   Bank  Bar  Baseball Field  Basketball Court  Beach  Big Box Store  Bistro  \
0     0    0               0                 0      0              0       0   
1     0    0               0                 0      0              0       0   
2     0    0               0                 0      0              0       0   
3     0    0               0                 0      0              0       0   
4     0    0               0                 0      0              0       0   

   Board Shop  Boat or Ferry  Bookstore  Boutique  Bowling Alley  \
0           0              0          0         0              0   
1           0              0          0         0              0   
2           0              0          0         0              0   
3           0              0          0         0              0   
4           0              0          0         0              0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Buffet  Building  Burger Joint  Burrito Place  Bus Line  \
0                0       0         0             0              0         0   
1                0       0         0             0              0         0   
2                0       0         0             0              0         0   
3                0       0         0             0           

And let's examine the new dataframe size.

In [28]:
la_onehot.shape

(2974, 323)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [29]:
la_grouped = la_onehot.groupby('Neighborhood').mean().reset_index()
la_grouped

Neighborhood       ATM  Accessories Store  \
0                                    Acton  0.000000           0.000000   
1                          Adams-Normandie  0.000000           0.000000   
2                             Agoura Hills  0.000000           0.000000   
3                               Agua Dulce  0.000000           0.000000   
4                                 Alhambra  0.000000           0.000000   
5                             Alondra Park  0.000000           0.000000   
6                                 Altadena  0.000000           0.000000   
7                                  Arcadia  0.000000           0.000000   
8                                   Arleta  0.000000           0.000000   
9                        Arlington Heights  0.000000           0.000000   
10                                 Artesia  0.000000           0.000000   
11                                  Athens  0.000000           0.000000   
12                         Atwater Village  0.045455           0.000000   
13                                  Avalon  0.000000           0.000000   
14                         Avocado Heights  0.000000           0.000000   
15                                   Azusa  0.000000           0.000000   
16                  Baldwin Hills/Crenshaw  0.000000           0.000000   
17                            Baldwin Park  0.000000           0.000000   
18                                 Bel-Air  0.000000           0.000000   
19                                    Bell  0.000000           0.000000   
20                            Bell Gardens  0.000000           0.000000   
21                              Bellflower  0.000000           0.000000   
22                           Beverly Grove  0.000000           0.010000   
23                           Beverly Hills  0.000000           0.000000   
24                             Beverlywood  0.000000           0.000000   
25                           Boyle Heights  0.000000           0.000000   
26                                Bradbury  0.000000           0.000000   
27                               Brentwood  0.000000           0.000000   
28                     Broadway-Manchester  0.000000           0.000000   
29                                 Burbank  0.000000           0.000000   
30                               Calabasas  0.000000           0.000000   
31                             Canoga Park  0.000000           0.000000   
32                                 Carthay  0.000000           0.000000   
33                         Central-Alameda  0.000000           0.000000   
34                            Century City  0.000000           0.000000   
35                                Cerritos  0.000000           0.000000   
36                             Charter Oak  0.000000           0.000000   
37                              Chatsworth  0.000000           0.000000   
38                     Chesterfield Square  0.000000           0.000000   
39                           Cheviot Hills  0.000000           0.000000   
40                               Chinatown  0.000000           0.000000   
41                                  Citrus  0.000000           0.000000   
42                                Commerce  0.000000           0.000000   
43                                 Compton  0.000000           0.000000   
44                                  Covina  0.000000           0.000000   
45                                  Cudahy  0.000000           0.000000   
46                             Culver City  0.000000           0.000000   
47                            Cypress Park  0.000000           0.000000   
48                                Del Aire  0.000000           0.000000   
49                                 Del Rey  0.000000           0.000000   
50                             Diamond Bar  0.000000           0.000000   
51                                  Downey  0.023256           0.000000   
52                                Downtown  0.000000   

#### Let's confirm the new size

In [30]:
la_grouped.shape

(238, 323)

#### Let's print each neighborhood along with the top 5 most common venues

In [31]:
num_top_venues = 5

for hood in la_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = la_grouped[la_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Acton----
                        venue  freq
0  Construction & Landscaping   1.0
1                         ATM   0.0
2                      Office   0.0
3       Performing Arts Venue   0.0
4                        Park   0.0


----Adams-Normandie----
              venue  freq
0  Sushi Restaurant   0.3
1       Yoga Studio   0.1
2       Gas Station   0.1
3     Grocery Store   0.1
4        Taco Place   0.1


----Agoura Hills----
                  venue  freq
0  Fast Food Restaurant  0.15
1        Breakfast Spot  0.07
2    Chinese Restaurant  0.07
3         Grocery Store  0.04
4         Shopping Mall  0.04


----Agua Dulce----
                   venue  freq
0                Airport   1.0
1                    ATM   0.0
2                 Notary   0.0
3  Performing Arts Venue   0.0
4                   Park   0.0


----Alhambra----
                  venue  freq
0     Convenience Store  0.29
1            Bagel Shop  0.07
2             Pet Store  0.07
3  Fast Food Restaurant  0.07
4    Mexi

#### Let's put that into a *pandas* dataframe

First, let's write a function to sort the venues in descending order.

In [32]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [33]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = la_grouped['Neighborhood']

for ind in np.arange(la_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(la_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood       1st Most Common Venue 2nd Most Common Venue  \
0            Acton  Construction & Landscaping           Yoga Studio   
1  Adams-Normandie            Sushi Restaurant           Yoga Studio   
2     Agoura Hills        Fast Food Restaurant    Chinese Restaurant   
3       Agua Dulce                     Airport           Yoga Studio   
4         Alhambra           Convenience Store   Sporting Goods Shop   

        3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0          Falafel Restaurant     Electronics Store   Empanada Restaurant   
1                  Playground                  Park            Taco Place   
2              Breakfast Spot                 Hotel          Burger Joint   
3                        Farm     Electronics Store   Empanada Restaurant   
4  Construction & Landscaping            Bagel Shop             Pet Store   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0    English Restaurant           Escape Room  Ethiopian Restaurant   
1         Grocery Store             Bookstore           Gas Station   
2                Bakery       Thai Restaurant      Sushi Restaurant   
3    English Restaurant           Escape Room  Ethiopian Restaurant   
4        Breakfast Spot           Video Store           Pizza Place   

  9th Most Common Venue 10th Most Common Venue  
0           Fabric Shop                Factory  
1                  Farm         Farmers Market  
2                Lounge                Brewery  
3           Fabric Shop                Factory  
4  Fast Food Restaurant         Hardware Store

<a id='item4'></a>

## 4. Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [34]:
# set number of clusters
kclusters = 5

la_grouped_clustering = la_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(la_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 1, 1, 1, 1, 2, 1, 1, 1, 1], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [35]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
# neighborhoods_venues_sorted.head()
la_merged = neighborhoods
# merge la_grouped with la_data to add latitude/longitude for each neighborhood
la_merged = la_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')
la_merged = la_merged.fillna(0)
la_merged = la_merged.astype({"Cluster Labels": int})
la_merged.head() # check first 5 rows

Neighborhood   Latitude   Longitude  Cluster Labels  \
0            Acton  34.497355 -118.169810               0   
1  Adams-Normandie  34.031461 -118.300208               1   
2     Agoura Hills  34.146736 -118.759885               1   
3       Agua Dulce  34.504927 -118.317104               1   
4         Alhambra  34.085539 -118.136512               1   

        1st Most Common Venue 2nd Most Common Venue  \
0  Construction & Landscaping           Yoga Studio   
1            Sushi Restaurant           Yoga Studio   
2        Fast Food Restaurant    Chinese Restaurant   
3                     Airport           Yoga Studio   
4           Convenience Store   Sporting Goods Shop   

        3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0          Falafel Restaurant     Electronics Store   Empanada Restaurant   
1                  Playground                  Park            Taco Place   
2              Breakfast Spot                 Hotel          Burger Joint   
3                        Farm     Electronics Store   Empanada Restaurant   
4  Construction & Landscaping            Bagel Shop             Pet Store   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0    English Restaurant           Escape Room  Ethiopian Restaurant   
1         Grocery Store             Bookstore           Gas Station   
2                Bakery       Thai Restaurant      Sushi Restaurant   
3    English Restaurant           Escape Room  Ethiopian Restaurant   
4        Breakfast Spot           Video Store           Pizza Place   

  9th Most Common Venue 10th Most Common Venue  
0           Fabric Shop                Factory  
1                  Farm         Farmers Market  
2                Lounge                Brewery  
3           Fabric Shop                Factory  
4  Fast Food Restaurant         Hardware Store

Finally, let's visualize the resulting clusters

In [36]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(la_merged['Latitude'], la_merged['Longitude'], la_merged['Neighborhood'], la_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

<a id='item5'></a>

## 5. Examine Clusters

Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, you can then assign a name to each cluster. I will leave this exercise to you.

#### Cluster 1

In [44]:
la_merged.loc[la_merged['Cluster Labels'] == 0, la_merged.columns[[0] + list(range(4, la_merged.shape[1]))]]

Neighborhood       1st Most Common Venue  \
0                                    Acton  Construction & Landscaping   
8                            Angeles Crest                           0   
25                           Beverly Crest                           0   
37                                  Carson                           0   
39                         Castaic Canyons                           0   
41                                 Castaic                           0   
46                    Chatsworth Reservoir                           0   
51                               Claremont                           0   
62                   Desert View Highlands                           0   
66                                  Duarte                           0   
98                              Hansen Dam                           0   
104                          Hasley Canyon  Construction & Landscaping   
108                           Hidden Hills                           0   
125                       La Habra Heights  Construction & Landscaping   
127                            Lake Hughes                           0   
128                       Lake Los Angeles  Construction & Landscaping   
129                      Lake View Terrace                           0   
139                           Leona Valley                           0   
144                    Lopez/Kagel Canyons                           0   
151                      Mayflower Village  Construction & Landscaping   
162              Northeast Antelope Valley                           0   
166              Northwest Antelope Valley                           0   
167                     Northwest Palmdale                           0   
174                               Palmdale                           0   
190                  Rolling Hills Estates                           0   
193                            Ridge Route                           0   
194                          Rolling Hills                           0   
207                            Sun Village                           0   
209                           Shadow Hills                           0   
214                      South Diamond Bar                           0   
215              Southeast Antelope Valley                           0   
222                         South Whittier                           0   
224                        Stevenson Ranch                           0   
234                        Tujunga Canyons                           0   
236         Unincorporated Catalina Island                           0   
245  Unincorporated Santa Susana Mountains                           0   
249                View Park-Windsor Hills                           0   
250                                Vincent                           0   
265                               Whittier                           0   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0             Yoga Studio    Falafel Restaurant     Electronics Store   
8                       0                     0                     0   
25                      0                     0                     0   
37                      0                     0                     0   
39                      0                     0                     0   
41                      0                     0                     0   
46                      0                     0                     0   
51                      0                     0                     0   
62                      0                     0                     0   
66                      0                     0                     0   
98                      0                     0                     0   
104           Yoga Studio    Falafel Restaurant     Electronics Store   
108                     0                     0                     0   
125           Yoga Studio    Falafel Restaurant

#### Cluster 2

In [45]:
la_merged.loc[la_merged['Cluster Labels'] == 1, la_merged.columns[[0] + list(range(4, la_merged.shape[1]))]]

Neighborhood      1st Most Common Venue  \
1             Adams-Normandie           Sushi Restaurant   
2                Agoura Hills       Fast Food Restaurant   
3                  Agua Dulce                    Airport   
4                    Alhambra          Convenience Store   
6                     Artesia          Indian Restaurant   
7                    Altadena               Home Service   
9                     Arcadia             Cosmetics Shop   
10                     Arleta                     Bakery   
11          Arlington Heights          Korean Restaurant   
13            Atwater Village                 Taco Place   
14                     Avalon                Golf Course   
15            Avocado Heights         Mexican Restaurant   
16                      Azusa     Thrift / Vintage Store   
17            Vermont-Slauson               Burger Joint   
19               Baldwin Park     Thrift / Vintage Store   
21                 Bellflower                Pizza Place   
22               Bell Gardens                       Park   
24                       Bell                   Wine Bar   
26              Beverly Grove             Clothing Store   
27                    Burbank         Mexican Restaurant   
28                  Koreatown          Korean Restaurant   
29              Beverly Hills                 Food Truck   
30                Beverlywood              Historic Site   
31              Boyle Heights              Grocery Store   
33                  Brentwood             Scenic Lookout   
34        Broadway-Manchester       Gym / Fitness Center   
35                  Calabasas                 Bagel Shop   
36                Canoga Park         Mexican Restaurant   
38                    Carthay       Ethiopian Restaurant   
42            Central-Alameda                       Food   
43               Century City                Coffee Shop   
44                   Cerritos                 Food Truck   
47        Chesterfield Square               Burger Joint   
48              Cheviot Hills       Other Great Outdoors   
49                  Chinatown         Chinese Restaurant   
50                     Citrus         Italian Restaurant   
52                 Northridge              Hot Dog Joint   
53                   Commerce             Cosmetics Shop   
54                    Compton       Fast Food Restaurant   
55               Cypress Park                       Park   
56                  La Mirada                    Theater   
57                     Covina               Burger Joint   
58                     Cudahy               Burger Joint   
59                Culver City                        Gym   
60                   Del Aire                        Gym   
61                    Del Rey         Mexican Restaurant   
63                Diamond Bar         Chinese Restaurant   
64                     Downey               Burger Joint   
65                   Downtown                Flower Shop   
67                 Eagle Rock                       Pool   
68               East Compton         Mexican Restaurant   
69             East Hollywood                     Bakery   
70             East La Mirada         Chinese Restaurant   
71             Elizabeth Lake                       Lake   
72           East Los Angeles         Mexican Restaurant   
73              East Pasadena           Basketball Court   
74           East San Gabriel          Fish & Chips Shop   
75                  Echo Park                       Café   
76                   El Monte          Mobile Phone Shop   
77                 El Segundo                  Pet Store   
78                  El Sereno                        ATM   
79               Elysian Park                       Park   
80             Elysian Valley                      Trail   
81             Vermont Square               Burger Joint   
82                     Encino              Deli / Bodega   
83            Exposition Park                       Food 

#### Cluster 3

In [46]:
la_merged.loc[la_merged['Cluster Labels'] == 2, la_merged.columns[[0] + list(range(4, la_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
5               Alondra Park                  Park          Cycle Studio   
18    Baldwin Hills/Crenshaw                  Park        Clothing Store   
40                Chatsworth            Playground                  Park   
96          Hacienda Heights                  Park          Cycle Studio   
102             Harvard Park        Shipping Store                  Park   
115          Huntington Park          Burger Joint   Fried Chicken Joint   
122    La Crescenta-Montrose                  Park          Cycle Studio   
135                 La Verne                  Pool                  Park   
155            Mission Hills                Church      Basketball Court   
160        Montecito Heights                  Park                  Lake   
184             Porter Ranch                  Park          Home Service   
216           South El Monte    Mexican Restaurant            Playground   
218               South Park                  Park          Cycle Studio   
226                  Sunland                  Park            Bagel Shop   
242                Val Verde                  Park     Convenience Store   
248  Veterans Administration                  Park            Food Truck   
262           West San Dimas                  Park     Other Repair Shop   
266         Whittier Narrows                  Park                  Lake   

           3rd Most Common Venue        4th Most Common Venue  \
5    Eastern European Restaurant            Electronics Store   
18                   Music Venue                  Yoga Studio   
40                   Yoga Studio                      Factory   
96   Eastern European Restaurant            Electronics Store   
102   Financial or Legal Service                  Film Studio   
115                         Park                  Yoga Studio   
122  Eastern European Restaurant            Electronics Store   
135                  Yoga Studio                      Factory   
155                         Park                  Yoga Studio   
160  Eastern European Restaurant            Electronics Store   
184                       Lawyer                   Water Park   
216                         Park                  Yoga Studio   
218  Eastern European Restaurant            Electronics Store   
226                  Yoga Studio            Electronics Store   
242                      Factory  Eastern European Restaurant   
248                 Intersection                  Film Studio   
262                  Flea Market  Eastern European Restaurant   
266  Eastern European Restaurant            Electronics Store   

           5th Most Common Venue        6th Most Common Venue  \
5            Empanada Restaurant           English Restaurant   
18                       Factory            Electronics Store   
40   Eastern European Restaurant            Electronics Store   
96           Empanada Restaurant           English Restaurant   
102          Dumpling Restaurant  Eastern European Restaurant   
115                      Factory            Electronics Store   
122          Empanada Restaurant           English Restaurant   
135  Eastern European Restaurant            Electronics Store   
155                      Factory            Electronics Store   
160          Empanada Restaurant           English Restaurant   
184                  Fabric Shop  Eastern European Restaurant   
216                      Factory  Eastern European Restaurant   
218          Empanada Restaurant           English Restaurant   
226          Empanada Restaurant           English Restaurant   
242            Electronics Store          Empanada Restaurant   
248          Filipino Restaurant  Eastern European Restaurant   
262            Electronics Store          Empanada Restaurant   
266          Empanada Restaurant           English Restaurant   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
5             Escape Room 

#### Cluster 4

In [47]:
la_merged.loc[la_merged['Cluster Labels'] == 3, la_merged.columns[[0] + list(range(4, la_merged.shape[1]))]]

Neighborhood 1st Most Common Venue       2nd Most Common Venue  \
12                 Athens          Home Service                 Yoga Studio   
20                Bel-Air          Home Service            Football Stadium   
23           Green Valley            Playground                Home Service   
32               Bradbury               Stables                Home Service   
45            Charter Oak                  Park                Home Service   
94          Granada Hills          Home Service  Construction & Landscaping   
156         Monterey Park           Art Gallery                Home Service   
198             San Dimas                  Food                Cycle Studio   
221  South San Jose Hills          Home Service                 Candy Store   
247                Vernon          Home Service                        Food   

      3rd Most Common Venue        4th Most Common Venue  \
12       Falafel Restaurant            Electronics Store   
20                 Dive Bar                  Yoga Studio   
23                     Food           Falafel Restaurant   
32       Falafel Restaurant  Eastern European Restaurant   
45                    Field                      Factory   
94              Yoga Studio           Falafel Restaurant   
156             Yoga Studio            Electronics Store   
198       Electronics Store          Empanada Restaurant   
221             Yoga Studio           Falafel Restaurant   
247  Furniture / Home Store           Falafel Restaurant   

           5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
12           Empanada Restaurant    English Restaurant           Escape Room   
20            Falafel Restaurant   Empanada Restaurant    English Restaurant   
23             Electronics Store   Empanada Restaurant    English Restaurant   
32             Electronics Store   Empanada Restaurant    English Restaurant   
45   Eastern European Restaurant     Electronics Store   Empanada Restaurant   
94             Electronics Store   Empanada Restaurant    English Restaurant   
156          Empanada Restaurant    English Restaurant           Escape Room   
198           English Restaurant           Escape Room  Ethiopian Restaurant   
221            Electronics Store   Empanada Restaurant    English Restaurant   
247            Electronics Store   Empanada Restaurant    English Restaurant   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
12   Ethiopian Restaurant           Fabric Shop                Factory  
20            Escape Room  Ethiopian Restaurant            Fabric Shop  
23            Escape Room  Ethiopian Restaurant            Fabric Shop  
32            Escape Room  Ethiopian Restaurant            Fabric Shop  
45     English Restaurant           Escape Room   Ethiopian Restaurant  
94            Escape Room  Ethiopian Restaurant            Fabric Shop  
156  Ethiopian Restaurant           Fabric Shop                Factory  
198           Fabric Shop               Factory     Falafel Restaurant  
221           Escape Room  Ethiopian Restaurant            Fabric Shop  
247           Escape Room  Ethiopian Restaurant            Fabric Shop

#### Cluster 5

In [48]:
la_merged.loc[la_merged['Cluster Labels'] == 4, la_merged.columns[[0] + list(range(4, la_merged.shape[1]))]]

Neighborhood 1st Most Common Venue  \
91                                Glendale                 Trail   
161                       Mount Washington                 Trail   
191                    Rancho Palos Verdes                 Trail   
211                           Sierra Madre                 Trail   
235                                Tujunga                  Lake   
241  Unincorporated Santa Monica Mountains                 Trail   

    2nd Most Common Venue 3rd Most Common Venue        4th Most Common Venue  \
91               Pharmacy           Yoga Studio                      Factory   
161                Garden                  Park                  Yoga Studio   
191           Yoga Studio               Factory  Eastern European Restaurant   
211     Other Repair Shop          Gourmet Shop                  Coffee Shop   
235                 Trail               Factory  Eastern European Restaurant   
241           Yoga Studio               Factory  Eastern European Restaurant   

    5th Most Common Venue        6th Most Common Venue 7th Most Common Venue  \
91      Electronics Store          Empanada Restaurant    English Restaurant   
161           Fabric Shop  Eastern European Restaurant     Electronics Store   
191     Electronics Store          Empanada Restaurant    English Restaurant   
211           Yoga Studio          Dumpling Restaurant     Electronics Store   
235     Electronics Store          Empanada Restaurant    English Restaurant   
241     Electronics Store          Empanada Restaurant    English Restaurant   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
91            Escape Room  Ethiopian Restaurant            Fabric Shop  
161   Empanada Restaurant    English Restaurant            Escape Room  
191           Escape Room  Ethiopian Restaurant            Fabric Shop  
211   Empanada Restaurant    English Restaurant            Escape Room  
235           Escape Room  Ethiopian Restaurant            Fabric Shop  
241           Escape Room  Ethiopian Restaurant            Fabric Shop